In [1]:
from Database import db_mongo

from Utilities import clean_text

import string

db = db_mongo.db_mongo()

df = db.get_text_full_resume(100000000)

df = df.sample(frac=1).reset_index(drop=True)

Init DB


In [2]:
ct = clean_text.CleanText()

df['text'] = ct.cleanner_process(df["text"])

[nltk_data] Downloading package wordnet to /home/kguttas/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
# Import gensim modules.
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from gensim.models import KeyedVectors
from gensim.scripts.glove2word2vec import glove2word2vec
import pandas as pd
import numpy as np

# Tagging documents. Each sentences(set of words) are mapped unique index.
# Tagged documents are input for doc2vec model. 
tagged_documents = []
for i, doc in enumerate(df['text']):
    tagged = TaggedDocument(doc, [i])
    tagged_documents.append(tagged)

In [4]:
new_sentence = """Java Developer

We are rapidly expanding our North American presence, currently searching for a number of technical resources, including a Java Developer highly skilled in server-side Java and Oracle SQL.

In this role you'll contribute to the development of new SaaS products and new features within existing products, operating primarily in the backend and contributing across the stack as your skills and interests dictate.

Location:

You’ll work remotely, collaborating with colleagues In the US, Canada and India.

Essential Qualifications:

4+ years of core Java and Oracle SQL development experience.
Experienced in, and well-suited to a waterfall development environment.
Strong understanding of the software development lifecycle.
A natural problem-solver; driven; quick to learn.
Positive, collaborative and constructive; a true team player."""


new_sentence = ct.cleanner_process(new_sentence)

new_sentence = new_sentence[0].split(" ")

tagged = TaggedDocument(new_sentence, [i])
tagged_documents.append(tagged)

In [5]:
tagged_documents

[TaggedDocument(words='LABORER Summary utilize knowledge experience obtain management level position organization leveraging abilities increase success organization that return allows advancement personal achievement Highlights Dependable reliable worker Ability assess solve problems quickly Extensive experience with project management SelfStarter able maintain motivation with littleno supervision Works well team lead member group Detail oriented Vastly creative Quick adaptation tasks direction Ability work stressful conditions Ability multitask fast pace environment Ability successfully meet project deadlines Organized Highly motivated Accomplishments Army Commendation Medalreceived times Autreve Award Runnerup Experience February Current Company Name City State Laborer Laborer duties consisted forming pouring concrete sidewalks floors commercial parking lots walls Able load unload material grading digging while operating skid loader While working Nehring maintained level safety compl

In [16]:

    
# Create doc2vec model.
model = Doc2Vec(vector_size=300, window=7, min_count=1, workers=-1)

model.build_vocab(tagged_documents)

model.dv.vectors_lockf = np.ones(len(model.dv), dtype= np.float64)

glove_file = 'data/glove.840B.300d.txt'
word2vec_file = 'data/GoogleNews-vectors-negative300.bin'
tmp_file = "data/test_word2vec.txt"

#_ = glove2word2vec(glove_file, tmp_file)

# model = KeyedVectors.load_word2vec_format(glove_file, binary=False, no_header=True)

In [21]:
model.corpus_total_words

12303661

/home/kguttas/anaconda3/envs/practica/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `init_sims` (Gensim 4.0.0 implemented internal optimizations that make calls to init_sims() unnecessary. init_sims() is now obsoleted and will be completely removed in future versions. See https://github.com/RaRe-Technologies/gensim/wiki/Migrating-from-Gensim-3.x-to-4).
  """Entry point for launching an IPython kernel.


In [17]:

model.dv.intersect_word2vec_format(word2vec_file, lockf=1.0, binary=True)


In [19]:
%time
model.train(tagged_documents, total_examples=model.corpus_count, epochs = 200)


CPU times: user 2 µs, sys: 0 ns, total: 2 µs
Wall time: 3.81 µs


In [9]:
#model.save("data/doc2vec_recommender_resume.bin")

In [10]:
#model = Doc2Vec.load("data/doc2vec_recommender_resume.bin") 

In [20]:
# Create new sentence and vectorize it. 
new_sentence = """Java Developer

We are rapidly expanding our North American presence, currently searching for a number of technical resources, including a Java Developer highly skilled in server-side Java and Oracle SQL.

In this role you'll contribute to the development of new SaaS products and new features within existing products, operating primarily in the backend and contributing across the stack as your skills and interests dictate.

Essential Qualifications:

4+ years of core Java and Oracle SQL development experience.
Experienced in, and well-suited to a waterfall development environment.
Strong understanding of the software development lifecycle.
A natural problem-solver; driven; quick to learn.
Positive, collaborative and constructive; a true team player."""


new_sentence = ct.cleanner_process(new_sentence)

new_sentence = new_sentence[0].split(" ")

new_sentence_vectorized = model.infer_vector(new_sentence)

# Calculate cosine similarity. 
similar_sentences = model.dv.most_similar(positive=[new_sentence_vectorized])

# Output
output = []
for i, v in enumerate(similar_sentences):
    index = v[0]
    #output.append([i + 1, common_texts[index], v[1]])
    output.append([i + 1, df['text'][i], v[1]])
    
    df['text']
    
pd.DataFrame(output, columns=["rank", "common_texts", "cosine_similarity"])

rank                                       common_texts  cosine_similarity
0     1  LABORER Summary utilize knowledge experience o...           0.183367
1     2  BUSINESS DEVELOPMENT MANAGER Highlights BUSINE...           0.175188
2     3  PASTRY CHEF SERVER Summary main goal ensure th...           0.175076
3     4  DRIVERMANAGER Professional Summary years total...           0.159546
4     5  LEAD DESIGNER Career Focus professional with e...           0.157858
5     6   LEVEL ASSISTANT STORE MANAGER OPERATIONS MANA...           0.157056
6     7  ASSISTANT TEACHER Summary Teachers Aide loving...           0.156697
7     8  TEACHER Summary Dedicated teaching counseling ...           0.155919
8     9  SENIOR RESIDENT INSPECTOR Summary Dependable h...           0.149692
9    10  LICENSED HEALTHCARE COMMUNICATOR Summary obtai...           0.148917